<a href="https://colab.research.google.com/github/giannicito/stock-price-prediction-prophet/blob/main/predict.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [9]:
import math
import pandas_datareader as web
import numpy as np
import pandas as pd

from datetime import datetime, timedelta

from fbprophet import Prophet
import plotly.graph_objs as go

In [10]:
stock_names = {
    "Tesla" : "TSLA",
    "Google" : "GOOG",
    "Microsoft" : "MSFT",
    "Nvidia" : "NVDA",
    "Oil" : "CL=F",
    "Gold" : "GC=F",
    "Bitcoin" : "BTC-USD",
    "Nasdaq100" : "NQ=F",
    "Amazon" : "AMZN",
    "Facebook" : "FB",
    "Netflix" : "NFLX",
    "Apple" : "AAPL",
    "Zoom" : "ZM"
}

start_date = "2001-01-01"
last_date = datetime.strftime(datetime.now() - timedelta(1), '%Y-%m-%d')

In [11]:
def PerformPrediction( stock_name, stock_id ):
  # download the dataframe from yahoo finance, getting data from the 'start_date' to the 'last_date'
  df = web.DataReader( stock_id, data_source='yahoo', start=start_date, end=last_date ) 

  # move the index of the dataframe to a new column of the dataframe
  df.reset_index(inplace=True,drop=False)

  # Select only the important features needed for the purpose, that is, date and adjusted price
  data = df[["Date","Adj Close"]]

  # to fit the model, we need to rename the features (columns of the dataset) as those needed from Prophet
  data = data.rename(columns = {"Date":"ds","Adj Close":"y"}) 

  # let's create the Prophet model, setting the daily seasonality to true
  m = Prophet(daily_seasonality = True)
  m.fit(data) # fit the model using all data

  # we specify the number of days of future predictions
  future = m.make_future_dataframe(periods=365) 
  forecast_data = m.predict(future)

  # once get the forecasted data, we move again the date column to the index, both for the real and forecasted data
  data.set_index('ds', inplace=True)
  data.index = pd.to_datetime( data.index )

  forecast_data.set_index('ds', inplace=True)
  forecast_data.index = pd.to_datetime( forecast_data.index )

  # joining values with the predicted ones from the model, including expected price, upper and lower bound 
  viz_df = data.join(forecast_data[['yhat', 'yhat_lower','yhat_upper']], how = 'outer')

  # we start plotting the data in order to see the trend found from our model, even for future period of time 
  trace1 = go.Scatter(
      x = data.index,
      y = data[ "y" ],
      line = dict( color = "black" ),
      mode = 'lines',
      name = 'Real Data'
  )

  trace2 = go.Scatter(
      x = forecast_data.index,
      y = forecast_data[ "yhat" ],
      line = dict( color = "blue" ),
      mode = 'lines',
      name = 'Prediction'
  )

  trace3 = go.Scatter(
      x = viz_df.index,
      y = viz_df[ "yhat_upper" ],
      line = dict( color = "green" ),
      mode = 'lines',
      name = 'Upper Bound'
  )

  trace4 = go.Scatter(
      x = viz_df.index,
      y = viz_df[ "yhat_lower" ],
      line = dict( color = "red" ),
      mode = 'lines',
      name = 'Lower Bound'
  )

  layout = go.Layout(
      title = str( stock_name ),
      xaxis = {
          'title' : "Date"
      },
      yaxis = {'title' : "Close"}
  )

  fig = go.Figure(data=[trace1, trace2, trace3, trace4], layout=layout)
  fig.show()

  print( "\n\n" )

In [12]:
for k in stock_names.keys():
  PerformPrediction( k, stock_names[ k ] )

INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
